In [2]:
import pandas as pd
import numpy as np
import datetime
import pickle
import requests

## 1. 데이터 전처리 과정
- 데이터들의 결과값으로 **월별 읍면동 쓰레기 총량**을 출력해내야 함
  - 따라서 모든 제공 데이터의 기준을 **월별 읍면동**으로 인덱스(그룹핑)화 시키는 과정을 거쳤다.

- 제공 데이터의 이름을 적절히 변경한 후 데이터프레임으로 변환하는 과정을 거침
1. 쓰레기 데이터 : food_waste
2. 카드 소비 데이터 : card_spending
3. 거주인구 데이터 : resident
4. 장기체류 외국인 유동인구 데이터 : long_term_frgn
5. 단기체류 외국인 유동인구 데이터 : short_term_frgn
6. 내국인 유동인구 데이터 : korean

In [10]:
waste=pd.read_csv("./datas/food_waste.csv",encoding='CP949',low_memory=False)
waste.head()

base_date city    emd_cd emd_nm em_area_cd  em_cnt   em_g  pay_amt
0  2018-01-01  제주시  50110670    외도동     W6X062       2  15500      464
1  2018-01-01  제주시  50110630    아라동     W6XA97      25  59800     1787
2  2018-01-01  제주시  50110630    아라동     W6XA96       8  25350      758
3  2018-01-01  제주시  50110630    아라동     W6XA95      12  30000      898
4  2018-01-01  제주시  50110630    아라동     W6XA94      14  44050     1317

In [4]:
card=pd.read_csv("./datas/card_spending.csv",encoding='CP949',low_memory=False)
card.head()

base_date city    emd_cd emd_nm mct_cat_cd mct_cat_nm  use_cnt    use_amt
0  2018-01-06  제주시  50110650     연동     C00100         한식     3643  127777300
1  2018-01-09  제주시  50110650     연동     C00500      패스트푸드      432    6711675
2  2018-01-15  제주시  50110650     연동     C01200      농축수산물      236   16089579
3  2018-01-15  제주시  50110650     연동     A00200    마트/슈퍼마켓     4031  121979867
4  2018-01-20  제주시  50110650     연동     C01000         식품      633   30410674

In [5]:
korean=pd.read_csv("./datas/korean.csv",encoding='CP949',low_memory=False)
korean.head()

base_date  time city    emd_cd emd_nm sex  age  resd_pop_cnt  \
0  2018-01-01     1  제주시  50110250    한림읍  여성    0      638.5509   
1  2018-01-01     1  제주시  50110250    한림읍  여성    0        0.0000   
2  2018-01-01     1  제주시  50110250    한림읍  여성   10      668.4577   
3  2018-01-01     1  제주시  50110250    한림읍  여성   10        0.0000   
4  2018-01-01     1  제주시  50110250    한림읍  여성   20      609.7710   

   work_pop_cnt  visit_pop_cnt resd  
0       15.5400       151.5149   제주  
1        3.7249       171.3458   그외  
2       17.0308       166.0500   제주  
3        4.2577       195.8539   그외  
4        5.9490       148.7246   제주

In [18]:
long_frgn=pd.read_csv("./datas/long_term_frgn.csv",encoding='CP949',low_memory=False)
long_frgn.head()

base_date  time nationality city    emd_cd emd_nm  resd_pop_cnt  \
0  2018-01-01     1         CAN  제주시  50110250    한림읍        6.3381   
1  2018-01-01     1         CHN  제주시  50110250    한림읍      442.1091   
2  2018-01-01     1         CHN  제주시  50110250    한림읍        0.0000   
3  2018-01-01     1         DEU  제주시  50110250    한림읍        0.0000   
4  2018-01-01     1         ETC  제주시  50110250    한림읍       15.9184   

   work_pop_cnt  visit_pop_cnt resd  
0        0.0000         4.5802   제주  
1        0.0000         5.7051   제주  
2        7.8695        51.3461   그외  
3        0.0000         8.2099   그외  
4        0.0000         2.8758   제주

In [7]:
short_frgn=pd.read_csv("./datas/short_term_frgn.csv",encoding='CP949',low_memory=False)
short_frgn.head()

base_date  time nationality city    emd_cd emd_nm  visit_pop_cnt
0  2018-01-01     1         CHN  제주시  50110250    한림읍        66.3170
1  2018-01-01     1         ETC  제주시  50110250    한림읍        21.1308
2  2018-01-01     1         HKG  제주시  50110250    한림읍         3.6771
3  2018-01-01     1         JPN  제주시  50110250    한림읍         5.5962
4  2018-01-01     1         USA  제주시  50110250    한림읍         3.9078

In [55]:
resident=pd.read_csv("./datas/resident.csv",encoding='CP949',low_memory=False)
resident.head()

base_year  base_month  city    emd_cd emd_nm sex  resid_reg_pop  \
0       2018           1   제주시  50110590    건입동  남성           5085   
1       2018           1   제주시  50110590    건입동  여성           4715   
2       2018           1   제주시  50110256    구좌읍  남성           7965   
3       2018           1   제주시  50110256    구좌읍  여성           7609   
4       2018           1  서귀포시  50130253    남원읍  남성           9806   

   foreign_pop  total_pop  
0          146       5231  
1           82       4797  
2          368       8333  
3          184       7793  
4          428      10234

- 모든 테이블을 전처리 하는 과정 중 범주형 변수는 one-hot encoding을 통하여 분석이 용이하도록 변경하였다.

### 1. food_waste 전처리

In [34]:
waste['base_date']=waste['base_date'].apply(lambda x:x[:7])#일 단위 삭제
waste_group=waste.groupby(['base_date','emd_nm']).sum()#월단위 읍면동 그룹핑
waste_group

em_cnt       em_g  pay_amt
base_date emd_nm                            
2018-01   건입동      18416   45646550  1364804
          남원읍       9570   42437700  1270773
          노형동     113990  265018400  7883340
          대륜동      21666   57612600  1676850
          대정읍      10185   38885550  1164122
...                  ...        ...      ...
2021-06   표선면      10751   42453750  1271419
          한경면       8031   27060150   809898
          한림읍      25653   82746990  2476292
          화북동      66088  110750050  3306029
          효돈동       8720   27554100   824457

[1666 rows x 3 columns]

- 기본적으로 모든 데이터들은 일별 단위이기 때문에 **base_date를 월 단위**로 바꾸어줄 필요가 있었다.
- 그 이후 모든 과정의 월별 읍면동으로 그룹핑하는 과정은 동일함

In [35]:
old_cols=list(waste_group.columns)#새로운 이름 붙여주기
new_cols=[]#각 키워드가 들어갈 리스트
for value in old_cols:
    value='waste_'+value
    new_cols.append(value)
waste_group.columns=new_cols
waste_group.head()

waste_em_cnt  waste_em_g  waste_pay_amt
base_date emd_nm                                         
2018-01   건입동            18416    45646550        1364804
          남원읍             9570    42437700        1270773
          노형동           113990   265018400        7883340
          대륜동            21666    57612600        1676850
          대정읍            10185    38885550        1164122

- 각 파일별로 중복된 이름이 있는 것을 확인함
  - 이를 구분하기 위해 각 변수에 키워드를 붙여 구분되도록 저장
  - 그 이후 과정에 모두 들어갈 예정임

### 2. long_term_frgn 전처리

In [21]:
long_frgn['base_date']=long_frgn['base_date'].apply(lambda x:x[:7])#일 단위 삭제
long_group=long_frgn.groupby(['base_date','emd_nm']).sum()#월단위 읍면동 그룹핑
long_assemble=long_group.drop(['emd_cd','time'],axis=1)#단순합이 가능한 변수가 담겨있는 데이터프레임
long_assemble.head()

resd_pop_cnt  work_pop_cnt  visit_pop_cnt
base_date emd_nm                                           
2018-01   건입동     1.018044e+05    16943.8851    115266.8745
          구좌읍     2.213694e+05    34858.6714    132749.8157
          남원읍     2.143870e+05    32056.8310    161791.6340
          노형동     1.401165e+06   120223.7692    418261.9018
          대륜동     1.119539e+05    10579.4808    130811.2037

In [22]:
long_count=long_frgn.drop(['emd_cd','resd_pop_cnt','work_pop_cnt','visit_pop_cnt','time'],axis=1)
long_count_temp=pd.get_dummies(long_count,columns=['nationality','resd','city'])#one-hot encoding
long_count_group=long_count_temp.groupby(['base_date','emd_nm']).sum()#클래스형 변수가 담겨있는 데이터프레임
long_count_group.head()

nationality_AUS  nationality_BGD  nationality_CAN  \
base_date emd_nm                                                      
2018-01   건입동                33.0             29.0            138.0   
          구좌읍                40.0              0.0            747.0   
          남원읍               107.0             10.0            147.0   
          노형동               761.0             57.0           1046.0   
          대륜동               563.0              0.0           1017.0   

                  nationality_CHN  nationality_DEU  nationality_EGY  \
base_date emd_nm                                                      
2018-01   건입동              1466.0              3.0              0.0   
          구좌읍              1486.0              0.0              0.0   
          남원읍              1488.0              0.0              3.0   
          노형동              1488.0             25.0             15.0   
          대륜동              1484.0            174.0              1.0   

                  nationality_ETC  nationality_FRA  nationality_GBR  \
base_date emd_nm                                                      
2018-01   건입동               755.0              3.0            101.0   
          구좌읍              1068.0             26.0             44.0   
          남원읍               598.0             33.0            144.0   
          노형동              1188.0            257.0            627.0   
          대륜동              1249.0             10.0            645.0   

                  nationality_IDN  ...  nationality_THA  nationality_TWN  \
base_date emd_nm                   ...                                     
2018-01   건입동              1471.0  ...             45.0            652.0   
          구좌읍              1468.0  ...            722.0            154.0   
          남원읍              1486.0  ...            231.0             27.0   
          노형동              1180.0  ...            976.0           1119.0   
          대륜동              1243.0  ...            111.0            693.0   

                  nationality_UKR  nationality_USA  nationality_UZB  \
base_date emd_nm                                                      
2018-01   건입동                 9.0            715.0            122.0   
          구좌읍                 7.0           1179.0            631.0   
          남원읍                 0.0            526.0            218.0   
          노형동                 6.0           1215.0            419.0   
          대륜동                 0.0            954.0            291.0   

                  nationality_VNM  resd_그외  resd_제주  city_서귀포시  city_제주시  
base_date emd_nm                                                          
2018-01   건입동              1471.0   4497.0   7363.0        0.0   11860.0  
          구좌읍              1479.0   6499.0   9945.0        0.0   16444.0  
          남원읍              1442.0   6790.0   7307.0    14097.0       0.0  
          노형동              1487.0   6687.0  13918.0        0.0   20605.0  
          대륜동              1205.0   5135.0   9330.0    14465.0       0.0  

[5 rows x 35 columns]

- 클래스형 변수를 따로 one-hot encoding 시켜줌

In [36]:
long_group_new=pd.concat([long_assemble,long_count_group],axis=1)
old_cols=list(long_group_new.columns)#새로운 이름 붙여주기
new_cols=[]#각 키워드가 들어갈 리스트
for value in old_cols:
    value='long_'+value
    new_cols.append(value)
long_group_new.columns=new_cols
long_group_new.head()

long_resd_pop_cnt  long_work_pop_cnt  long_visit_pop_cnt  \
base_date emd_nm                                                             
2018-01   건입동          1.018044e+05         16943.8851         115266.8745   
          구좌읍          2.213694e+05         34858.6714         132749.8157   
          남원읍          2.143870e+05         32056.8310         161791.6340   
          노형동          1.401165e+06        120223.7692         418261.9018   
          대륜동          1.119539e+05         10579.4808         130811.2037   

                  long_nationality_AUS  long_nationality_BGD  \
base_date emd_nm                                               
2018-01   건입동                     33.0                  29.0   
          구좌읍                     40.0                   0.0   
          남원읍                    107.0                  10.0   
          노형동                    761.0                  57.0   
          대륜동                    563.0                   0.0   

                  long_nationality_CAN  long_nationality_CHN  \
base_date emd_nm                                               
2018-01   건입동                    138.0                1466.0   
          구좌읍                    747.0                1486.0   
          남원읍                    147.0                1488.0   
          노형동                   1046.0                1488.0   
          대륜동                   1017.0                1484.0   

                  long_nationality_DEU  long_nationality_EGY  \
base_date emd_nm                                               
2018-01   건입동                      3.0                   0.0   
          구좌읍                      0.0                   0.0   
          남원읍                      0.0                   3.0   
          노형동                     25.0                  15.0   
          대륜동                    174.0                   1.0   

                  long_nationality_ETC  ...  long_nationality_THA  \
base_date emd_nm                        ...                         
2018-01   건입동                    755.0  ...                  45.0   
          구좌읍                   1068.0  ...                 722.0   
          남원읍                    598.0  ...                 231.0   
          노형동                   1188.0  ...                 976.0   
          대륜동                   1249.0  ...                 111.0   

                  long_nationality_TWN  long_nationality_UKR  \
base_date emd_nm                                               
2018-01   건입동                    652.0                   9.0   
          구좌읍                    154.0                   7.0   
          남원읍                     27.0                   0.0   
          노형동                   1119.0                   6.0   
          대륜동                    693.0                   0.0   

                  long_nationality_USA  long_nationality_UZB  \
base_date emd_nm                                               
2018-01   건입동                    715.0                 122.0   
          구좌읍                   1179.0                 631.0   
          남원읍                    526.0                 218.0   
          노형동                   1215.0                 419.0   
          대륜동                    954.0                 291.0   

                  long_nationality_VNM  long_resd_그외  long_resd_제주  \
base_date emd_nm                                                     
2018-01   건입동                   1471.0        4497.0        7363.0   
          구좌읍                   1479.0        6499.0        9945.0   
          남원읍                   1442.0        6790.0        7307.0   
          노형동                   1487.0        6687.0       13918.0   
          대륜동                   1205.0        5135.0        9330.0   

                  long_city_서귀포시  long_city_제주시  
base_date emd_nm                                 
2018-01   건입동                0.0        11860.0  
          구좌읍                0.0        16444.0  
          남원읍            14097.0            0.0  
 

### 3. short_term_frgn 전처리

In [25]:
short_frgn['base_date']=short_frgn['base_date'].apply(lambda x:x[:7])#일 단위 삭제
short_group=short_frgn.groupby(['base_date','emd_nm']).sum()#월단위 읍면동 그룹핑
short_assemble=short_group.drop(['emd_cd','time'],axis=1)#단순합이 가능한 변수가 담겨있는 데이터프레임
short_assemble.head()

visit_pop_cnt
base_date emd_nm               
2018-01   건입동        78223.0796
          구좌읍        46564.7514
          남원읍       255565.1599
          노형동       199557.9400
          대륜동        42826.8763

In [29]:
short_count=short_frgn.drop(['emd_cd','visit_pop_cnt','time'],axis=1)
short_count_temp=pd.get_dummies(short_count,columns=['nationality','city'])#one-hot encoding
short_count_group=short_count_temp.groupby(['base_date','emd_nm']).sum()#클래스형 변수가 담겨있는 데이터프레임
short_count_group.head()

nationality_CHN  nationality_ETC  nationality_HKG  \
base_date emd_nm                                                      
2018-01   건입동               744.0            627.0            383.0   
          구좌읍               744.0            540.0            123.0   
          남원읍               744.0            744.0            516.0   
          노형동               744.0            743.0            500.0   
          대륜동               742.0            660.0            216.0   

                  nationality_IDN  nationality_JPN  nationality_MYS  \
base_date emd_nm                                                      
2018-01   건입동               213.0            533.0            672.0   
          구좌읍               101.0            244.0            524.0   
          남원읍               173.0            526.0            557.0   
          노형동               161.0            527.0            730.0   
          대륜동               141.0            333.0            568.0   

                  nationality_SGP  nationality_THA  nationality_USA  \
base_date emd_nm                                                      
2018-01   건입동               538.0            239.0            289.0   
          구좌읍               245.0            216.0            483.0   
          남원읍               368.0            246.0            590.0   
          노형동               308.0            246.0            552.0   
          대륜동               222.0             28.0            230.0   

                  nationality_VNM  city_서귀포시  city_제주시  
base_date emd_nm                                        
2018-01   건입동                98.0        0.0    4336.0  
          구좌읍                 0.0        0.0    3220.0  
          남원읍               168.0     4632.0       0.0  
          노형동                57.0        0.0    4568.0  
          대륜동                 1.0     3141.0       0.0

In [37]:
short_group_new=pd.concat([short_assemble,short_count_group],axis=1)
old_cols=list(short_group_new.columns)#새로운 이름 붙여주기
new_cols=[]#각 키워드가 들어갈 리스트
for value in old_cols:
    value='short_'+value
    new_cols.append(value)
short_group_new.columns=new_cols
short_group_new.head()

short_visit_pop_cnt  short_nationality_CHN  \
base_date emd_nm                                               
2018-01   건입동              78223.0796                  744.0   
          구좌읍              46564.7514                  744.0   
          남원읍             255565.1599                  744.0   
          노형동             199557.9400                  744.0   
          대륜동              42826.8763                  742.0   

                  short_nationality_ETC  short_nationality_HKG  \
base_date emd_nm                                                 
2018-01   건입동                     627.0                  383.0   
          구좌읍                     540.0                  123.0   
          남원읍                     744.0                  516.0   
          노형동                     743.0                  500.0   
          대륜동                     660.0                  216.0   

                  short_nationality_IDN  short_nationality_JPN  \
base_date emd_nm                                                 
2018-01   건입동                     213.0                  533.0   
          구좌읍                     101.0                  244.0   
          남원읍                     173.0                  526.0   
          노형동                     161.0                  527.0   
          대륜동                     141.0                  333.0   

                  short_nationality_MYS  short_nationality_SGP  \
base_date emd_nm                                                 
2018-01   건입동                     672.0                  538.0   
          구좌읍                     524.0                  245.0   
          남원읍                     557.0                  368.0   
          노형동                     730.0                  308.0   
          대륜동                     568.0                  222.0   

                  short_nationality_THA  short_nationality_USA  \
base_date emd_nm                                                 
2018-01   건입동                     239.0                  289.0   
          구좌읍                     216.0                  483.0   
          남원읍                     246.0                  590.0   
          노형동                     246.0                  552.0   
          대륜동                      28.0                  230.0   

                  short_nationality_VNM  short_city_서귀포시  short_city_제주시  
base_date emd_nm                                                          
2018-01   건입동                      98.0              0.0          4336.0  
          구좌읍                       0.0              0.0          3220.0  
          남원읍                     168.0           4632.0             0.0  
          노형동                      57.0              0.0          4568.0  
          대륜동                       1.0           3141.0             0.0

### 4. korean 전처리

In [38]:
korean['base_date']=korean['base_date'].apply(lambda x:x[:7])#일 단위 삭제
korean_group=korean.groupby(['base_date','emd_nm']).sum()#월단위 읍면동 그룹핑
korean_assemble=korean_group.drop(['emd_cd','time','age'],axis=1)#단순합이 가능한 변수가 담겨있는 데이터프레임
korean_assemble.head()

resd_pop_cnt  work_pop_cnt  visit_pop_cnt
base_date emd_nm                                           
2018-01   건입동     4.935983e+06  7.039353e+05   4.938897e+06
          구좌읍     7.998788e+06  7.538520e+05   5.099720e+06
          남원읍     8.648312e+06  6.924429e+05   5.555027e+06
          노형동     3.630623e+07  3.592287e+06   1.526984e+07
          대륜동     8.274240e+06  8.105084e+05   6.600239e+06

In [42]:
korean_count=korean.drop(['city','emd_cd','resd_pop_cnt','work_pop_cnt','visit_pop_cnt'],axis=1)
korean_count_temp=pd.get_dummies(korean_count,columns=['sex','age','resd'])#one-hot encoding
korean_count_group=korean_count_temp.groupby(['base_date','emd_nm']).sum()#클래스형 변수가 담겨있는 데이터프레임
korean_count_group.head()

time   sex_남성   sex_여성   age_0  age_10  age_20  age_30  \
base_date emd_nm                                                             
2018-01   건입동     334084  13388.0  13338.0  2976.0  2976.0  2976.0  2976.0   
          구좌읍     334800  13392.0  13392.0  2976.0  2976.0  2976.0  2976.0   
          남원읍     334800  13392.0  13392.0  2976.0  2976.0  2976.0  2976.0   
          노형동     334800  13392.0  13392.0  2976.0  2976.0  2976.0  2976.0   
          대륜동     334800  13392.0  13392.0  2976.0  2976.0  2976.0  2976.0   

                  age_40  age_50  age_60  age_70  age_80  resd_그외  resd_제주  
base_date emd_nm                                                            
2018-01   건입동     2976.0  2976.0  2976.0  2947.0  2947.0  13334.0  13392.0  
          구좌읍     2976.0  2976.0  2976.0  2976.0  2976.0  13392.0  13392.0  
          남원읍     2976.0  2976.0  2976.0  2976.0  2976.0  13392.0  13392.0  
          노형동     2976.0  2976.0  2976.0  2976.0  2976.0  13392.0  13392.0  
          대륜동     2976.0  2976.0  2976.0  2976.0  2976.0  13392.0  13392.0

In [43]:
korean_group_new=pd.concat([korean_assemble,korean_count_group],axis=1)
old_cols=list(korean_group_new.columns)#새로운 이름 붙여주기
new_cols=[]#각 키워드가 들어갈 리스트
for value in old_cols:
    value='korean_'+value
    new_cols.append(value)
korean_group_new.columns=new_cols
korean_group_new.drop(['korean_time'],axis=1,inplace=True)
korean_group_new.head()

korean_resd_pop_cnt  korean_work_pop_cnt  \
base_date emd_nm                                             
2018-01   건입동            4.935983e+06         7.039353e+05   
          구좌읍            7.998788e+06         7.538520e+05   
          남원읍            8.648312e+06         6.924429e+05   
          노형동            3.630623e+07         3.592287e+06   
          대륜동            8.274240e+06         8.105084e+05   

                  korean_visit_pop_cnt  korean_time  korean_sex_남성  \
base_date emd_nm                                                     
2018-01   건입동             4.938897e+06       334084        13388.0   
          구좌읍             5.099720e+06       334800        13392.0   
          남원읍             5.555027e+06       334800        13392.0   
          노형동             1.526984e+07       334800        13392.0   
          대륜동             6.600239e+06       334800        13392.0   

                  korean_sex_여성  korean_age_0  korean_age_10  korean_age_20  \
base_date emd_nm                                                              
2018-01   건입동           13338.0        2976.0         2976.0         2976.0   
          구좌읍           13392.0        2976.0         2976.0         2976.0   
          남원읍           13392.0        2976.0         2976.0         2976.0   
          노형동           13392.0        2976.0         2976.0         2976.0   
          대륜동           13392.0        2976.0         2976.0         2976.0   

                  korean_age_30  korean_age_40  korean_age_50  korean_age_60  \
base_date emd_nm                                                               
2018-01   건입동            2976.0         2976.0         2976.0         2976.0   
          구좌읍            2976.0         2976.0         2976.0         2976.0   
          남원읍            2976.0         2976.0         2976.0         2976.0   
          노형동            2976.0         2976.0         2976.0         2976.0   
          대륜동            2976.0         2976.0         2976.0         2976.0   

                  korean_age_70  korean_age_80  korean_resd_그외  korean_resd_제주  
base_date emd_nm                                                                
2018-01   건입동            2947.0         2947.0         13334.0         13392.0  
          구좌읍            2976.0         2976.0         13392.0         13392.0  
          남원읍            2976.0         2976.0         13392.0         13392.0  
          노형동            2976.0         2976.0         13392.0         13392.0  
          대륜동            2976.0         2976.0         13392.0         13392.0

### 5. card 전처리

In [45]:
card['base_date']=card['base_date'].apply(lambda x:x[:7])#일 단위 삭제
card_label={'마트/슈퍼마켓':0,
           '한식':1,
           '양식':2,
           '아시아음식':3,
           '간식':4,
           '패스트푸드':5,
           '부페':6,
           '주점및주류판매':7,
           '식품':8,
           '농축수산물':9,
           '배달':10}

- 논문상에서 폐기되는 음식물의 양 또한 음식물의 종류에 따라 다르다는 것을 알게 됨
  - 이를 **카드에서 소비된 음식 종류**를 통해 간접적으로 알아보고자 함
  - 이를위한 새로운 변수/딕셔너리 생성

In [47]:
card['mct_cat_nm']=card['mct_cat_nm'].apply(lambda x:card_label[x])
card_du=pd.get_dummies(card,columns=['mct_cat_nm'])#one-hot encoding
list_=[]
for i in card_label.values():
    temp=card_du[card_du['mct_cat_nm_'+str(i)]==1].copy()
    temp['mct_cat_nm_'+str(i)]=temp['use_amt']
    temp.drop(['use_amt'],axis=1,inplace=True)
    list_.append(temp)
new_card=pd.concat(list_[:11])
new_card['base_date']=new_card['base_date'].apply(lambda s:s[:4]+'-'+s[5:7])
new_card.head()

base_date city    emd_cd emd_nm mct_cat_cd  use_cnt  mct_cat_nm_0  \
3    2018-01  제주시  50110650     연동     A00200     4031     121979867   
14   2018-02  제주시  50110650     연동     A00200     3364      99018979   
34   2018-04  제주시  50110650     연동     A00200     3532      94000829   
43   2018-05  제주시  50110650     연동     A00200     3153      81716456   
49   2018-05  제주시  50110650     연동     A00200     3901     133939526   

    mct_cat_nm_1  mct_cat_nm_2  mct_cat_nm_3  mct_cat_nm_4  mct_cat_nm_5  \
3              0             0             0             0             0   
14             0             0             0             0             0   
34             0             0             0             0             0   
43             0             0             0             0             0   
49             0             0             0             0             0   

    mct_cat_nm_6  mct_cat_nm_7  mct_cat_nm_8  mct_cat_nm_9  mct_cat_nm_10  
3              0             0             0             0              0  
14             0             0             0             0              0  
34             0             0             0             0              0  
43             0             0             0             0              0  
49             0             0             0             0              0

In [49]:
card_group=new_card.groupby(['base_date','emd_nm']).sum()
old_cols=list(card_group.columns)
new_cols=[]
for value in old_cols:
    value='card_'+value
    new_cols.append(value)
card_group.columns=new_cols
card_group.head()

card_use_cnt  card_mct_cat_nm_0  card_mct_cat_nm_1  \
base_date emd_nm                                                       
2018-01   건입동            57683          613458055          705583595   
          구좌읍            38869          468618011          441322929   
          남원읍            49138          700738510          545929908   
          노형동           397207         4918395521         4035120676   
          대륜동            65027         1204811433          670003378   

                  card_mct_cat_nm_2  card_mct_cat_nm_3  card_mct_cat_nm_4  \
base_date emd_nm                                                            
2018-01   건입동              37051483           69893850           52714107   
          구좌읍              31575817           52730081           24271899   
          남원읍              18314275           87237934           36003854   
          노형동             230258664          478343394          398428801   
          대륜동              38325300           92484907           62481472   

                  card_mct_cat_nm_5  card_mct_cat_nm_6  card_mct_cat_nm_7  \
base_date emd_nm                                                            
2018-01   건입동              55110922            5081850           14468297   
          구좌읍              36994936             735518            4325710   
          남원읍              57030976             836173            9074662   
          노형동             402990583           15383521          114581724   
          대륜동              81574888            1100822           10153389   

                  card_mct_cat_nm_8  card_mct_cat_nm_9  card_mct_cat_nm_10  
base_date emd_nm                                                            
2018-01   건입동             279219424          180535251            11571838  
          구좌읍             290942686           81939014             3714415  
          남원읍             285403473          132565191             5163749  
          노형동            1100095419          521442784            86216063  
          대륜동             110219574          133506435             9839787

### 6. resident 전처리

- resident의 경우 다른 데이터와 다르게 월단위로 이미 지정되어 있어 이름/변수를 단순 변형하기만 하면 됐다.

In [56]:
old_cols=list(resident.columns)
new_cols=[]
for value in old_cols:
    value='resident_'+value
    new_cols.append(value)
resident.columns=new_cols
resident.head()

resident_base_year  resident_base_month resident_city  resident_emd_cd  \
0                2018                    1           제주시         50110590   
1                2018                    1           제주시         50110590   
2                2018                    1           제주시         50110256   
3                2018                    1           제주시         50110256   
4                2018                    1          서귀포시         50130253   

  resident_emd_nm resident_sex  resident_resid_reg_pop  resident_foreign_pop  \
0             건입동           남성                    5085                   146   
1             건입동           여성                    4715                    82   
2             구좌읍           남성                    7965                   368   
3             구좌읍           여성                    7609                   184   
4             남원읍           남성                    9806                   428   

   resident_total_pop  
0                5231  
1                4797  
2                8333  
3                7793  
4               10234

In [57]:
resident['resident_base_month']=resident['resident_base_month'].apply(lambda x:str(x).zfill(2))#월을 두자리수로 변경
resident['resident_base_year']=resident['resident_base_year'].astype(str)#년도를 스트링타입으로 변경
resident['base_date']=resident['resident_base_year']+'-'+resident['resident_base_month']#새로운 기준일 생성
resident['emd_nm']=resident['resident_emd_nm']#컬럼 이름 변경 귀찮아서 생성 후 삭제
resident.drop(['resident_base_year','resident_base_month','resident_emd_nm'],axis=1,inplace=True)#필요없는 변수 삭제
resident_group=resident.groupby(['base_date','emd_nm']).sum()#월단위 읍면동 그룹핑
resident_group.head()

resident_emd_cd  resident_resid_reg_pop  \
base_date emd_nm                                            
2018-01   건입동           100221180                    9800   
          구좌읍           100220512                   15574   
          남원읍           100260506                   19112   
          노형동           100221320                   53369   
          대륜동           100261180                   13473   

                  resident_foreign_pop  resident_total_pop  
base_date emd_nm                                            
2018-01   건입동                      228               10028  
          구좌읍                      552               16126  
          남원읍                      628               19740  
          노형동                     1589               54958  
          대륜동                      178               13651

- 모든 파일 전처리 과정 완료. 각 파일들을 csv 형태로 저장하도록 함

In [58]:
waste_group.to_csv("./datas/waste_group.csv")
card_group.to_csv("./datas/card_group.csv")
long_group_new.to_csv("./datas/long_group.csv")
short_group_new.to_csv("./datas/short_group.csv")
korean_group_new.to_csv("./datas/korean_group.csv")
resident_group.to_csv("./datas/resident_group.csv")

## 2. 외부 데이터 활용

- 관련 논문을 찾아보던 도중 RFID 방식을 이용하는 형태의 음식물쓰레기 배출량이 상대적으로 적다는 논문을 보게 됨
  - 이에 RFID 관련 데이터를 도출하여 프로그램에 사용토록 함

### 1. 아파트 코드 알아내기
- 장비별 배출량을 알아내기 위해서는 각 아파트의 코드를 알아내야만 했다.
  - 이 또한 api 상에서 검색이 가능했기에 아파트 코드 테이블을 먼저 만들도록 한다.

In [ ]:
dong=['한림읍','애월읍','구좌읍','조천읍','한경면','일도1동','일도2동','이도1동','이도2동','삼도1동',
      '삼도2동','용담1동','용담2동','건입동','화북동','삼양동','봉개동','아라동','오라동',
     '연동','노형동','외도동','이호동','도두동','대정읍','남원읍','성산읍','안덕면','표선면',
     '송산동','정방동','중앙동','천지동','효돈동','영천동','동홍동','서홍동','대륜동','대천동',
     '중문동','예래동']

In [22]:
decode='' #api 주소값
sulist=[]
for value in dataSu:
    tempdict={'aptCode':value['aptCode'],'aptName':value['aptName'],'aptMemo':value['aptMemo'],
             'citySggName':value['citySggName']}
    tempdict['emd_nm']=None #기본 법정동 검색 가이드
    for dongvar in dong:
        if value['aptName'] is not None and value['aptName'].find(dongvar) != -1:
            tempdict['emd_nm']=dongvar
            break
        elif value['aptMemo'] is not None and value['aptMemo'].find(dongvar) != -1:
            tempdict['emd_nm']=dongvar
            break    
    sulist.append(tempdict)
sudf=pd.DataFrame(data=sulist)
sudf

aptCode        aptName   aptMemo citySggName emd_nm
0    W6Y001  동홍동 일호 3차 아파트      None        서귀포시    동홍동
1    W6Y002     동홍동 노인복지회관      None        서귀포시    동홍동
2    W6Y003      동홍동 대림아파트      None        서귀포시    동홍동
3    W6Y004  동홍동 주공 2차 아파트      None        서귀포시    동홍동
4    W6Y005  동홍동 세기아파트(1차)      None        서귀포시    동홍동
..      ...            ...       ...         ...    ...
726  W6Y747   태흥3리 재활용도움센터  태흥리 63-1        서귀포시   None
727  W6Y748  산이수동버스정류장(BM)      None        서귀포시   None
728  W6Y74A       힘찬해가(BM)      None        서귀포시   None
729  W6Y74B    동홍동센트레빌(BM)      None        서귀포시    동홍동
730  W6YFFF           해당없음      삭제엄금        서귀포시   None

[731 rows x 5 columns]

In [27]:
dataJe=resp.json()['data']['list']
jelist=[]
for value in dataJe:
    tempdict={'aptCode':value['aptCode'],'aptName':value['aptName'],'aptMemo':value['aptMemo'],
             'citySggName':value['citySggName']}
    tempdict['emd_nm']=None #기본 법정동 검색 가이드
    for dongvar in dong:
        if value['aptName'] is not None and value['aptName'].find(dongvar) != -1:
            tempdict['emd_nm']=dongvar
            break
        elif value['aptMemo'] is not None and value['aptMemo'].find(dongvar) != -1:
            tempdict['emd_nm']=dongvar
            break    
    jelist.append(tempdict)
jedf=pd.DataFrame(data=jelist)
jedf

aptCode        aptName                     aptMemo citySggName emd_nm
0     W6X000            제주시                        None         제주시   None
1     W6X001           건입현대                        None         제주시   None
2     W6X002          노형뜨란채                        None         제주시   None
3     W6X003          노형이편한                        None         제주시   None
4     W6X004           노형중흥                        None         제주시   None
...      ...            ...                         ...         ...    ...
2000  W6XFFB  조천읍 거치대 신촌-12      신촌북3길 43(닭머루 동측방면 거치대)         제주시    조천읍
2001  W6XFFC  조천읍 거치대 신촌-13  신촌서5길 103 (까사델마마 북측방향 주차장)         제주시    조천읍
2002  W6XFFD  조천읍 거치대 신촌-14   신촌서5길 92 (신촌교회 북측200M 지점)         제주시    조천읍
2003  W6XFFE  조천읍 거치대 신촌-17  신촌북1길 16 (신촌교회 동측100M 삼거리)         제주시    조천읍
2004  W6XFFF           해당없음                        삭제엄금         제주시   None

[2005 rows x 5 columns]

- 2~3시간정도의 정성적 처리 과정을 통해 각 row 별 emd_nm 값을 알아낼 수 있었다.
- 재가공된 파일을 이용하여 다시 api 값을 추출해보도록 하자
- emd_nm이 지정되지 않은 row값 삭제
  - 검색 자체가 안 되거나, 아파트 이름/메모 동시 누락, 어떤 아파트인지를 특정할 수 없는 경우, 다른 읍면동에 해당되는 경우 제외

In [28]:
jedf[jedf['emd_nm'].isna()]

Unnamed: 0 aptCode     aptName               aptMemo citySggName emd_nm
0              0  W6X000         제주시                   NaN         제주시    NaN
9              9  W6X009        도련주공                   NaN         제주시    NaN
17            17  W6X011       영산홍연립                   NaN         제주시    NaN
37            37  W6X025  용두암현대1차아파트                   NaN         제주시    NaN
57            57  W6X039    제일일출연립주택                   NaN         제주시    NaN
...          ...     ...         ...                   ...         ...    ...
1580        1580  W6XD13   한라산골프장빌리지  19년 8월 제주시 오등동 10-28         제주시    NaN
1729        1729  W6XE5D         이디연                 정한테크㈜         제주시    NaN
1734        1734  W6XE64      브리즈스테이               해안동32-7         제주시    NaN
1953        1953  W6XFAB       해링턴코트                 정한테크㈜         제주시    NaN
2004        2004  W6XFFF        해당없음                  삭제엄금         제주시    NaN

[92 rows x 6 columns]

In [26]:
sudf[sudf['emd_nm'].isna()]

Unnamed: 0 aptCode               aptName           aptMemo citySggName  \
40           40  W6Y042             풍림빌리지(BM)               NaN        서귀포시   
41           41  W6Y043             서진아파트(BM)               NaN        서귀포시   
50           50  W6Y053            중문월드연립(BM)         대포동 759-1        서귀포시   
107         107  W6Y113           새서귀포재활용도움센터         법환동 731-2        서귀포시   
137         137  W6Y143             유승한내들(BM)               NaN        서귀포시   
187         187  W6Y193           강정마을재활용도움센터        강정동 4362번지        서귀포시   
192         192  W6Y198        마을서쪽자비사가는길(BM)   서귀포시 하원동 1204-1        서귀포시   
193         193  W6Y199            하원동 예가(BM)       서귀포시 법화로 37        서귀포시   
194         194  W6Y200  마을회관입구 앞(AN빌라 남)(BM)       서귀포시 법화로 13        서귀포시   
239         239  W6Y246          상예마을회관 옆(BM)               NaN        서귀포시   
248         248  W6Y255           새마을금고서쪽(BM)             적치장-2        서귀포시   
249         249  W6Y256          하예하동마을회관(BM)                \n        서귀포시   
283         283  W6Y291             DM하우스(BM)            아파트 단지        서귀포시   
284         284  W6Y292            노인복지타운(BM)           적치장 - 6        서귀포시   
297         297  W6Y305             약천사입구(BM)               NaN        서귀포시   
305         305  W6Y313             천지공영주차빌딩앞               NaN        서귀포시   
308         308  W6Y316       서귀포 사랑으로 부영(BM)               NaN        서귀포시   
316         316  W6Y327             강정 LH 아파트  2016년 11월 11대 설치        서귀포시   
318         318  W6Y329            중흥S클래스(BM)               NaN        서귀포시   
320         320  W6Y331                시에나리조트      2016년 12월 설치        서귀포시   
321         321  W6Y332               강정골드클레스  2016년 12월 보광건설설치        서귀포시   
427         427  W6Y452       동일리준광역클린하우스(BM)               NaN        서귀포시   
429         429  W6Y454               서귀포데이즈힐         (주)솔루션아이티        서귀포시   
430         430  W6Y455            광진블리스힐(BM)               NaN        서귀포시   
437         437  W6Y462              중문천마에코피아           (주)콘포테크        서귀포시   
438         438  W6Y463               브리타니 토평         (주)솔루션아이티        서귀포시   
442         442  W6Y467               신시가지 군족               NaN        서귀포시   
446         446  W6Y46B                  행복주택               NaN        서귀포시   
505         505  W6Y527                 파출소 옆               NaN        서귀포시   
632         632  W6Y654           호근동 재활용도움센터               NaN        서귀포시   
647         647  W6Y669            (자체설치)루멘하임           (주)콘포테크        서귀포시   
648         648  W6Y66A              가온누리(BM)               NaN        서귀포시   
649         649  W6Y670            (자체설치)파라디빌             ㈜콘포테크        서귀포시   
650         650  W6Y671            (자체설치)서홍진용             ㈜콘포테크        서귀포시   
652         652  W6Y673           강정코아루2차(BM)               NaN        서귀포시   
656         656  W6Y677                 디자인주택               NaN        서귀포시   
657         657  W6Y678         하원마을회관 뒤쪽(BM)               NaN        서귀포시   
658         658  W6Y685               서호 블루오션               NaN        서귀포시   
659         659  W6Y686               상지 에코빌                NaN        서귀포시   
660         660  W6Y687             중문농협 용흥지소               NaN        서귀포시   
665         665  W6Y692              더그라벨 아파트               NaN        서귀포시   
666         666  W6Y693           서귀포법환코아루아파트         (주)솔루션아이티        서귀포시   
668         668  W6Y695                 모아캔빌라           (주)콘포테크        서귀포시   
686         686  W6Y714               S&P어린이집               NaN        서귀포시   
687         687  W6Y715       신흥1리 중형 재활용도움센터               NaN        서귀포시   
710         710  W6Y72D         색달동 재활용센터(BM)           재활용센터\n        서귀포시   
713         713  W6Y731            토평 솔레어더테라스               NaN        서귀포시   
714         714  W6Y732                  브리타니          2021년 4월        서귀포시   
730         730  W6YFFF                  해당없음              삭제엄금        서귀포시   

    emd_nm  
40     NaN  
41     NaN  
50     NaN  
10

In [27]:
sudf.drop(index=sudf[sudf['emd_nm'].isna()].index,inplace=True)
sudf

Unnamed: 0 aptCode        aptName       aptMemo citySggName emd_nm
0             0  W6Y001  동홍동 일호 3차 아파트           NaN        서귀포시    동홍동
1             1  W6Y002     동홍동 노인복지회관           NaN        서귀포시    동홍동
2             2  W6Y003      동홍동 대림아파트           NaN        서귀포시    동홍동
3             3  W6Y004  동홍동 주공 2차 아파트           NaN        서귀포시    동홍동
4             4  W6Y005  동홍동 세기아파트(1차)           NaN        서귀포시    동홍동
..          ...     ...            ...           ...         ...    ...
725         725  W6Y746          일번지가든  대정읍클린하우스73\n        서귀포시    대정읍
726         726  W6Y747   태흥3리 재활용도움센터      태흥리 63-1        서귀포시    남원읍
727         727  W6Y748  산이수동버스정류장(BM)           NaN        서귀포시    대정읍
728         728  W6Y74A       힘찬해가(BM)           NaN        서귀포시    안덕면
729         729  W6Y74B    동홍동센트레빌(BM)           NaN        서귀포시    동홍동

[682 rows x 6 columns]

In [29]:
jedf.drop(index=jedf[jedf['emd_nm'].isna()].index,inplace=True)
jedf

Unnamed: 0 aptCode        aptName                     aptMemo  \
1              1  W6X001           건입현대                         NaN   
2              2  W6X002          노형뜨란채                         NaN   
3              3  W6X003          노형이편한                         NaN   
4              4  W6X004           노형중흥                         NaN   
5              5  W6X005        대림이편한1차                         NaN   
...          ...     ...            ...                         ...   
1999        1999  W6XFFA  조천읍 거치대 신촌-11  신촌북2길 38-14 (대수동노인정 동측70M)   
2000        2000  W6XFFB  조천읍 거치대 신촌-12      신촌북3길 43(닭머루 동측방면 거치대)   
2001        2001  W6XFFC  조천읍 거치대 신촌-13  신촌서5길 103 (까사델마마 북측방향 주차장)   
2002        2002  W6XFFD  조천읍 거치대 신촌-14   신촌서5길 92 (신촌교회 북측200M 지점)   
2003        2003  W6XFFE  조천읍 거치대 신촌-17  신촌북1길 16 (신촌교회 동측100M 삼거리)   

     citySggName emd_nm  
1            제주시    건입동  
2            제주시    노형동  
3            제주시    노형동  
4            제주시    노형동  
5            제주시     연동  
...          ...    ...  
1999         제주시    조천읍  
2000         제주시    조천읍  
2001         제주시    조천읍  
2002         제주시    조천읍  
2003         제주시    조천읍  

[1913 rows x 6 columns]

- emd_nm 값인 빠진 데이터 프레임 생성. 이제 필요없는 프레임 삭제 후 api 사용함

In [30]:
jedf.drop(['aptName','aptMemo','citySggName'],axis=1,inplace=True)
sudf.drop(['aptName','aptMemo','citySggName'],axis=1,inplace=True)
jedf.head()

aptCode emd_nm
1  W6X001    건입동
2  W6X002    노형동
3  W6X003    노형동
4  W6X004    노형동
5  W6X005     연동

### 2. 각 장비의 배출량 구하기

In [32]:
inpath="C:/Users/mitha/OneDrive/바탕 화면/su1st.csv" #파일 불러오기 경로. su1st나 je1st 둘 중에 하나만 사용
#su1st : 서귀포시-682 row 존재 , je1st : 제주시-1913개 row 존재

sudf=pd.read_csv(inpath)
sudf.drop(['Unnamed: 0'],axis=1,inplace=True)

#teimdelta에서 제공하는 날짜 추가는 일단위까지만 지워하였기 때문에 월별로 넘기기 위한 전용 함수가 필요했다.
one=[1,3,5,7,8,10,12]#31일인 날
two=[4,6,9,11]#30일인 날
def date_set(month,year):
    if month in one:
        return 31
    elif month in two:
        return 30
    elif year%4==0:
        return 29
    else:
        return 28
    
suApt=list(sudf['aptCode'])
suEmd=list(sudf['emd_nm'])
suApt=suApt[start:end]
suEmd=suEmd[start:end]
sulist=[]

for i,code in enumerate(suApt):
    end_point=datetime.datetime(2021,7,1)#중단점 설정
    start_point=datetime.datetime(2018,1,1)#시작점 설정
    while end_point!=start_point:
        endpoint='http://apis.data.go.kr/B552584/RfidFoodWasteServiceNew/getCityAptDateList?ServiceKey={}&type=json&page=1&rowNum=100&disYear={}&disMonth={}&cityCode=W6Y&aptCode={}'.format(decode,start_point.year,str(start_point.month).zfill(2),code)
        resp = requests.get(endpoint)
        if resp.status_code == 200 and resp.json()['data']['count'] != 0:#불러오기 완료
            print(str(start_point.year)+'년 '+str(start_point.month).zfill(2)+'월의 '+code+'자료')
            data=resp.json()['data']['list']
            disCountsum=0
            disQuansum=0
            for value in data:
                disQuansum+=value['disQuantity']
                disCountsum+=value['disCount']
            sulist.append({'base_date':str(start_point.year)+'-'+str(start_point.month).zfill(2),'aptCode':code,'emd_nm':suEmd[i],'disQuantity':disQuansum,'disCount':disCountsum})
        else:#불러오기 실패
            print(str(start_point.year)+'년 '+str(start_point.month).zfill(2)+'월의 '+code+'자료가 불러와지지 않음')
            sulist.append({'base_date':str(start_point.year)+'-'+str(start_point.month).zfill(2),'aptCode':code,'emd_nm':suEmd[i]})
        start_point+=datetime.timedelta(days=date_set(start_point.month,start_point.year))
        
df_new_su=pd.DataFrame(data=sulist)

2018년 01월의 W6Y001자료
2018년 02월의 W6Y001자료
2018년 03월의 W6Y001자료
2018년 04월의 W6Y001자료
2018년 05월의 W6Y001자료
2018년 06월의 W6Y001자료
2018년 07월의 W6Y001자료
2018년 08월의 W6Y001자료
2018년 09월의 W6Y001자료
2018년 10월의 W6Y001자료
2018년 11월의 W6Y001자료
2018년 12월의 W6Y001자료
2019년 01월의 W6Y001자료
2019년 02월의 W6Y001자료
2019년 03월의 W6Y001자료
2019년 04월의 W6Y001자료
2019년 05월의 W6Y001자료
2019년 06월의 W6Y001자료
2019년 07월의 W6Y001자료
2019년 08월의 W6Y001자료
2019년 09월의 W6Y001자료
2019년 10월의 W6Y001자료
2019년 11월의 W6Y001자료
2019년 12월의 W6Y001자료
2020년 01월의 W6Y001자료
2020년 02월의 W6Y001자료
2020년 03월의 W6Y001자료
2020년 04월의 W6Y001자료
2020년 05월의 W6Y001자료
2020년 06월의 W6Y001자료
2020년 07월의 W6Y001자료
2020년 08월의 W6Y001자료
2020년 09월의 W6Y001자료
2020년 10월의 W6Y001자료
2020년 11월의 W6Y001자료
2020년 12월의 W6Y001자료
2021년 01월의 W6Y001자료
2021년 02월의 W6Y001자료
2021년 03월의 W6Y001자료
2021년 04월의 W6Y001자료가 불러와지지 않음
2021년 05월의 W6Y001자료
2021년 06월의 W6Y001자료
2018년 01월의 W6Y002자료
2018년 02월의 W6Y002자료
2018년 03월의 W6Y002자료
2018년 04월의 W6Y002자료
2018년 05월의 W6Y002자료
2018년 06월의 W6Y002자료
2018년 07월의 W6Y002자료
2018년 08월의

2019년 12월의 W6Y010자료
2020년 01월의 W6Y010자료
2020년 02월의 W6Y010자료
2020년 03월의 W6Y010자료
2020년 04월의 W6Y010자료
2020년 05월의 W6Y010자료
2020년 06월의 W6Y010자료
2020년 07월의 W6Y010자료
2020년 08월의 W6Y010자료
2020년 09월의 W6Y010자료
2020년 10월의 W6Y010자료
2020년 11월의 W6Y010자료
2020년 12월의 W6Y010자료
2021년 01월의 W6Y010자료
2021년 02월의 W6Y010자료
2021년 03월의 W6Y010자료
2021년 04월의 W6Y010자료가 불러와지지 않음
2021년 05월의 W6Y010자료
2021년 06월의 W6Y010자료
2018년 01월의 W6Y011자료
2018년 02월의 W6Y011자료
2018년 03월의 W6Y011자료
2018년 04월의 W6Y011자료
2018년 05월의 W6Y011자료
2018년 06월의 W6Y011자료
2018년 07월의 W6Y011자료
2018년 08월의 W6Y011자료
2018년 09월의 W6Y011자료
2018년 10월의 W6Y011자료
2018년 11월의 W6Y011자료
2018년 12월의 W6Y011자료
2019년 01월의 W6Y011자료
2019년 02월의 W6Y011자료
2019년 03월의 W6Y011자료가 불러와지지 않음
2019년 04월의 W6Y011자료가 불러와지지 않음
2019년 05월의 W6Y011자료
2019년 06월의 W6Y011자료
2019년 07월의 W6Y011자료
2019년 08월의 W6Y011자료
2019년 09월의 W6Y011자료
2019년 10월의 W6Y011자료
2019년 11월의 W6Y011자료
2019년 12월의 W6Y011자료
2020년 01월의 W6Y011자료
2020년 02월의 W6Y011자료
2020년 03월의 W6Y011자료
2020년 04월의 W6Y011자료
2020년 05월의 W6Y011자료
2020년 06월의

2021년 02월의 W6Y019자료가 불러와지지 않음
2021년 03월의 W6Y019자료가 불러와지지 않음
2021년 04월의 W6Y019자료가 불러와지지 않음
2021년 05월의 W6Y019자료가 불러와지지 않음
2021년 06월의 W6Y019자료
2018년 01월의 W6Y020자료
2018년 02월의 W6Y020자료
2018년 03월의 W6Y020자료
2018년 04월의 W6Y020자료
2018년 05월의 W6Y020자료
2018년 06월의 W6Y020자료
2018년 07월의 W6Y020자료
2018년 08월의 W6Y020자료
2018년 09월의 W6Y020자료
2018년 10월의 W6Y020자료
2018년 11월의 W6Y020자료
2018년 12월의 W6Y020자료
2019년 01월의 W6Y020자료
2019년 02월의 W6Y020자료
2019년 03월의 W6Y020자료
2019년 04월의 W6Y020자료가 불러와지지 않음
2019년 05월의 W6Y020자료
2019년 06월의 W6Y020자료
2019년 07월의 W6Y020자료
2019년 08월의 W6Y020자료
2019년 09월의 W6Y020자료
2019년 10월의 W6Y020자료
2019년 11월의 W6Y020자료
2019년 12월의 W6Y020자료
2020년 01월의 W6Y020자료
2020년 02월의 W6Y020자료
2020년 03월의 W6Y020자료
2020년 04월의 W6Y020자료
2020년 05월의 W6Y020자료
2020년 06월의 W6Y020자료
2020년 07월의 W6Y020자료
2020년 08월의 W6Y020자료
2020년 09월의 W6Y020자료
2020년 10월의 W6Y020자료
2020년 11월의 W6Y020자료
2020년 12월의 W6Y020자료
2021년 01월의 W6Y020자료
2021년 02월의 W6Y020자료
2021년 03월의 W6Y020자료
2021년 04월의 W6Y020자료가 불러와지지 않음
2021년 05월의 W6Y020자료
2021년 06월의 W6Y020자료


2020년 02월의 W6Y028자료
2020년 03월의 W6Y028자료
2020년 04월의 W6Y028자료
2020년 05월의 W6Y028자료
2020년 06월의 W6Y028자료
2020년 07월의 W6Y028자료
2020년 08월의 W6Y028자료
2020년 09월의 W6Y028자료
2020년 10월의 W6Y028자료
2020년 11월의 W6Y028자료
2020년 12월의 W6Y028자료
2021년 01월의 W6Y028자료
2021년 02월의 W6Y028자료
2021년 03월의 W6Y028자료
2021년 04월의 W6Y028자료가 불러와지지 않음
2021년 05월의 W6Y028자료
2021년 06월의 W6Y028자료
2018년 01월의 W6Y029자료
2018년 02월의 W6Y029자료
2018년 03월의 W6Y029자료
2018년 04월의 W6Y029자료
2018년 05월의 W6Y029자료
2018년 06월의 W6Y029자료
2018년 07월의 W6Y029자료
2018년 08월의 W6Y029자료
2018년 09월의 W6Y029자료
2018년 10월의 W6Y029자료
2018년 11월의 W6Y029자료
2018년 12월의 W6Y029자료
2019년 01월의 W6Y029자료
2019년 02월의 W6Y029자료가 불러와지지 않음
2019년 03월의 W6Y029자료가 불러와지지 않음
2019년 04월의 W6Y029자료가 불러와지지 않음
2019년 05월의 W6Y029자료
2019년 06월의 W6Y029자료
2019년 07월의 W6Y029자료
2019년 08월의 W6Y029자료
2019년 09월의 W6Y029자료
2019년 10월의 W6Y029자료
2019년 11월의 W6Y029자료
2019년 12월의 W6Y029자료
2020년 01월의 W6Y029자료
2020년 02월의 W6Y029자료
2020년 03월의 W6Y029자료
2020년 04월의 W6Y029자료
2020년 05월의 W6Y029자료
2020년 06월의 W6Y029자료
2020년 07월의 W6Y029자료


2018년 07월의 W6Y038자료
2018년 08월의 W6Y038자료
2018년 09월의 W6Y038자료
2018년 10월의 W6Y038자료
2018년 11월의 W6Y038자료
2018년 12월의 W6Y038자료
2019년 01월의 W6Y038자료
2019년 02월의 W6Y038자료
2019년 03월의 W6Y038자료
2019년 04월의 W6Y038자료가 불러와지지 않음
2019년 05월의 W6Y038자료
2019년 06월의 W6Y038자료
2019년 07월의 W6Y038자료
2019년 08월의 W6Y038자료
2019년 09월의 W6Y038자료
2019년 10월의 W6Y038자료
2019년 11월의 W6Y038자료
2019년 12월의 W6Y038자료
2020년 01월의 W6Y038자료
2020년 02월의 W6Y038자료
2020년 03월의 W6Y038자료
2020년 04월의 W6Y038자료
2020년 05월의 W6Y038자료
2020년 06월의 W6Y038자료
2020년 07월의 W6Y038자료
2020년 08월의 W6Y038자료
2020년 09월의 W6Y038자료
2020년 10월의 W6Y038자료
2020년 11월의 W6Y038자료
2020년 12월의 W6Y038자료
2021년 01월의 W6Y038자료
2021년 02월의 W6Y038자료
2021년 03월의 W6Y038자료
2021년 04월의 W6Y038자료가 불러와지지 않음
2021년 05월의 W6Y038자료
2021년 06월의 W6Y038자료
2018년 01월의 W6Y039자료
2018년 02월의 W6Y039자료
2018년 03월의 W6Y039자료
2018년 04월의 W6Y039자료
2018년 05월의 W6Y039자료
2018년 06월의 W6Y039자료
2018년 07월의 W6Y039자료
2018년 08월의 W6Y039자료
2018년 09월의 W6Y039자료
2018년 10월의 W6Y039자료
2018년 11월의 W6Y039자료
2018년 12월의 W6Y039자료
2019년 01월의 W6Y039자료


...

2019년 04월의 W6Y71D자료가 불러와지지 않음
2019년 05월의 W6Y71D자료가 불러와지지 않음
2019년 06월의 W6Y71D자료가 불러와지지 않음
2019년 07월의 W6Y71D자료가 불러와지지 않음
2019년 08월의 W6Y71D자료가 불러와지지 않음
2019년 09월의 W6Y71D자료가 불러와지지 않음
2019년 10월의 W6Y71D자료가 불러와지지 않음
2019년 11월의 W6Y71D자료가 불러와지지 않음
2019년 12월의 W6Y71D자료가 불러와지지 않음
2020년 01월의 W6Y71D자료가 불러와지지 않음
2020년 02월의 W6Y71D자료가 불러와지지 않음
2020년 03월의 W6Y71D자료가 불러와지지 않음
2020년 04월의 W6Y71D자료가 불러와지지 않음
2020년 05월의 W6Y71D자료가 불러와지지 않음
2020년 06월의 W6Y71D자료가 불러와지지 않음
2020년 07월의 W6Y71D자료
2020년 08월의 W6Y71D자료
2020년 09월의 W6Y71D자료
2020년 10월의 W6Y71D자료
2020년 11월의 W6Y71D자료
2020년 12월의 W6Y71D자료
2021년 01월의 W6Y71D자료
2021년 02월의 W6Y71D자료
2021년 03월의 W6Y71D자료
2021년 04월의 W6Y71D자료가 불러와지지 않음
2021년 05월의 W6Y71D자료
2021년 06월의 W6Y71D자료
2018년 01월의 W6Y71E자료가 불러와지지 않음
2018년 02월의 W6Y71E자료가 불러와지지 않음
2018년 03월의 W6Y71E자료가 불러와지지 않음
2018년 04월의 W6Y71E자료가 불러와지지 않음
2018년 05월의 W6Y71E자료가 불러와지지 않음
2018년 06월의 W6Y71E자료가 불러와지지 않음
2018년 07월의 W6Y71E자료가 불러와지지 않음
2018년 08월의 W6Y71E자료가 불러와지지 않음
2018년 09월의 W6Y71E자료가 불러와지지 않음
2018년 10월의 W6Y71E자료가 불러와지지 않음


2019년 07월의 W6Y724자료가 불러와지지 않음
2019년 08월의 W6Y724자료가 불러와지지 않음
2019년 09월의 W6Y724자료가 불러와지지 않음
2019년 10월의 W6Y724자료가 불러와지지 않음
2019년 11월의 W6Y724자료가 불러와지지 않음
2019년 12월의 W6Y724자료가 불러와지지 않음
2020년 01월의 W6Y724자료가 불러와지지 않음
2020년 02월의 W6Y724자료가 불러와지지 않음
2020년 03월의 W6Y724자료가 불러와지지 않음
2020년 04월의 W6Y724자료가 불러와지지 않음
2020년 05월의 W6Y724자료가 불러와지지 않음
2020년 06월의 W6Y724자료가 불러와지지 않음
2020년 07월의 W6Y724자료가 불러와지지 않음
2020년 08월의 W6Y724자료가 불러와지지 않음
2020년 09월의 W6Y724자료가 불러와지지 않음
2020년 10월의 W6Y724자료가 불러와지지 않음
2020년 11월의 W6Y724자료가 불러와지지 않음
2020년 12월의 W6Y724자료가 불러와지지 않음
2021년 01월의 W6Y724자료가 불러와지지 않음
2021년 02월의 W6Y724자료가 불러와지지 않음
2021년 03월의 W6Y724자료가 불러와지지 않음
2021년 04월의 W6Y724자료가 불러와지지 않음
2021년 05월의 W6Y724자료가 불러와지지 않음
2021년 06월의 W6Y724자료가 불러와지지 않음
2018년 01월의 W6Y725자료가 불러와지지 않음
2018년 02월의 W6Y725자료가 불러와지지 않음
2018년 03월의 W6Y725자료가 불러와지지 않음
2018년 04월의 W6Y725자료가 불러와지지 않음
2018년 05월의 W6Y725자료가 불러와지지 않음
2018년 06월의 W6Y725자료가 불러와지지 않음
2018년 07월의 W6Y725자료가 불러와지지 않음
2018년 08월의 W6Y725자료가 불러와지지 않음
2018년 09월의 W6Y725자료가 불러와지지 않음
2018년 10월의

2018년 04월의 W6Y72B자료가 불러와지지 않음
2018년 05월의 W6Y72B자료가 불러와지지 않음
2018년 06월의 W6Y72B자료가 불러와지지 않음
2018년 07월의 W6Y72B자료가 불러와지지 않음
2018년 08월의 W6Y72B자료가 불러와지지 않음
2018년 09월의 W6Y72B자료가 불러와지지 않음
2018년 10월의 W6Y72B자료가 불러와지지 않음
2018년 11월의 W6Y72B자료가 불러와지지 않음
2018년 12월의 W6Y72B자료가 불러와지지 않음
2019년 01월의 W6Y72B자료가 불러와지지 않음
2019년 02월의 W6Y72B자료가 불러와지지 않음
2019년 03월의 W6Y72B자료가 불러와지지 않음
2019년 04월의 W6Y72B자료가 불러와지지 않음
2019년 05월의 W6Y72B자료가 불러와지지 않음
2019년 06월의 W6Y72B자료가 불러와지지 않음
2019년 07월의 W6Y72B자료가 불러와지지 않음
2019년 08월의 W6Y72B자료가 불러와지지 않음
2019년 09월의 W6Y72B자료가 불러와지지 않음
2019년 10월의 W6Y72B자료가 불러와지지 않음
2019년 11월의 W6Y72B자료가 불러와지지 않음
2019년 12월의 W6Y72B자료가 불러와지지 않음
2020년 01월의 W6Y72B자료가 불러와지지 않음
2020년 02월의 W6Y72B자료가 불러와지지 않음
2020년 03월의 W6Y72B자료가 불러와지지 않음
2020년 04월의 W6Y72B자료가 불러와지지 않음
2020년 05월의 W6Y72B자료가 불러와지지 않음
2020년 06월의 W6Y72B자료가 불러와지지 않음
2020년 07월의 W6Y72B자료가 불러와지지 않음
2020년 08월의 W6Y72B자료가 불러와지지 않음
2020년 09월의 W6Y72B자료가 불러와지지 않음
2020년 10월의 W6Y72B자료가 불러와지지 않음
2020년 11월의 W6Y72B자료
2020년 12월의 W6Y72B자료
2021년 01월의 W6Y72B자료
2021년 02월의

2020년 10월의 W6Y735자료가 불러와지지 않음
2020년 11월의 W6Y735자료가 불러와지지 않음
2020년 12월의 W6Y735자료가 불러와지지 않음
2021년 01월의 W6Y735자료가 불러와지지 않음
2021년 02월의 W6Y735자료가 불러와지지 않음
2021년 03월의 W6Y735자료가 불러와지지 않음
2021년 04월의 W6Y735자료가 불러와지지 않음
2021년 05월의 W6Y735자료가 불러와지지 않음
2021년 06월의 W6Y735자료가 불러와지지 않음
2018년 01월의 W6Y736자료가 불러와지지 않음
2018년 02월의 W6Y736자료가 불러와지지 않음
2018년 03월의 W6Y736자료가 불러와지지 않음
2018년 04월의 W6Y736자료가 불러와지지 않음
2018년 05월의 W6Y736자료가 불러와지지 않음
2018년 06월의 W6Y736자료가 불러와지지 않음
2018년 07월의 W6Y736자료가 불러와지지 않음
2018년 08월의 W6Y736자료가 불러와지지 않음
2018년 09월의 W6Y736자료가 불러와지지 않음
2018년 10월의 W6Y736자료가 불러와지지 않음
2018년 11월의 W6Y736자료가 불러와지지 않음
2018년 12월의 W6Y736자료가 불러와지지 않음
2019년 01월의 W6Y736자료가 불러와지지 않음
2019년 02월의 W6Y736자료가 불러와지지 않음
2019년 03월의 W6Y736자료가 불러와지지 않음
2019년 04월의 W6Y736자료가 불러와지지 않음
2019년 05월의 W6Y736자료가 불러와지지 않음
2019년 06월의 W6Y736자료가 불러와지지 않음
2019년 07월의 W6Y736자료가 불러와지지 않음
2019년 08월의 W6Y736자료가 불러와지지 않음
2019년 09월의 W6Y736자료가 불러와지지 않음
2019년 10월의 W6Y736자료가 불러와지지 않음
2019년 11월의 W6Y736자료가 불러와지지 않음
2019년 12월의 W6Y736자료가 불러와지지 않음
2020년 01월의

2019년 04월의 W6Y745자료가 불러와지지 않음
2019년 05월의 W6Y745자료가 불러와지지 않음
2019년 06월의 W6Y745자료가 불러와지지 않음
2019년 07월의 W6Y745자료가 불러와지지 않음
2019년 08월의 W6Y745자료가 불러와지지 않음
2019년 09월의 W6Y745자료가 불러와지지 않음
2019년 10월의 W6Y745자료가 불러와지지 않음
2019년 11월의 W6Y745자료가 불러와지지 않음
2019년 12월의 W6Y745자료가 불러와지지 않음
2020년 01월의 W6Y745자료가 불러와지지 않음
2020년 02월의 W6Y745자료가 불러와지지 않음
2020년 03월의 W6Y745자료가 불러와지지 않음
2020년 04월의 W6Y745자료가 불러와지지 않음
2020년 05월의 W6Y745자료가 불러와지지 않음
2020년 06월의 W6Y745자료가 불러와지지 않음
2020년 07월의 W6Y745자료가 불러와지지 않음
2020년 08월의 W6Y745자료가 불러와지지 않음
2020년 09월의 W6Y745자료가 불러와지지 않음
2020년 10월의 W6Y745자료가 불러와지지 않음
2020년 11월의 W6Y745자료가 불러와지지 않음
2020년 12월의 W6Y745자료가 불러와지지 않음
2021년 01월의 W6Y745자료가 불러와지지 않음
2021년 02월의 W6Y745자료가 불러와지지 않음
2021년 03월의 W6Y745자료가 불러와지지 않음
2021년 04월의 W6Y745자료가 불러와지지 않음
2021년 05월의 W6Y745자료가 불러와지지 않음
2021년 06월의 W6Y745자료
2018년 01월의 W6Y746자료가 불러와지지 않음
2018년 02월의 W6Y746자료가 불러와지지 않음
2018년 03월의 W6Y746자료가 불러와지지 않음
2018년 04월의 W6Y746자료가 불러와지지 않음
2018년 05월의 W6Y746자료가 불러와지지 않음
2018년 06월의 W6Y746자료가 불러와지지 않음
2018년 07월의 W6Y746자료가

- 위는 서귀포시, 아래는 제주시

In [14]:
inpath="C:/Users/mitha/OneDrive/바탕 화면/je1st.csv" #파일 불러오기 경로. su1st나 je1st 둘 중에 하나만 사용
#su1st : 서귀포시-682 row 존재 , je1st : 제주시-1913개 row 존재

#end값이 row값 넘어가게 되면 인덱스 에러 발생. 470~682 범위에서는 None 요망
jeApt=list(jedf['aptCode'])
jeEmd=list(jedf['emd_nm'])
jelist=[]

for i,code in enumerate(jeApt):
    end_point=datetime.datetime(2021,7,1)#중단점 설정
    start_point=datetime.datetime(2018,1,1)#시작점 설정
    while end_point!=start_point:
        endpoint='http://apis.data.go.kr/B552584/RfidFoodWasteServiceNew/getCityAptDateList?ServiceKey={}&type=json&page=1&rowNum=100&disYear={}&disMonth={}&cityCode=W6X&aptCode={}'.format(decode,start_point.year,str(start_point.month).zfill(2),code)
        resp = requests.get(endpoint) 
        print(resp.status_code)
        if resp.status_code == 200 and resp.json()['data']['count'] != 0:#불러오기 완료
            print(str(start_point.year)+'년 '+str(start_point.month).zfill(2)+'월의 '+code+'자료')
            data=resp.json()['data']['list']
            disCountsum=0
            disQuansum=0
            for value in data:
                disQuansum+=value['disQuantity']
                disCountsum+=value['disCount']
            jelist.append({'base_date':str(start_point.year)+'-'+str(start_point.month).zfill(2),'aptCode':code,'emd_nm':jeEmd[i],'disQuantity':disQuansum,'disCount':disCountsum})
        else:#불러오기 오류
            print(str(start_point.year)+'년 '+str(start_point.month).zfill(2)+'월의 '+code+'자료가 불러와지지 않음')
            jelist.append({'base_date':str(start_point.year)+'-'+str(start_point.month).zfill(2),'aptCode':code,'emd_nm':jeEmd[i]})
        start_point+=datetime.timedelta(days=date_set(start_point.month,start_point.year))
        
df_new_je=pd.DataFrame(data=jelist)

200
2018년 01월의 W6X001자료가 불러와지지 않음
200
2018년 02월의 W6X001자료가 불러와지지 않음
200
2018년 03월의 W6X001자료가 불러와지지 않음
200
2018년 04월의 W6X001자료가 불러와지지 않음
200
2018년 05월의 W6X001자료가 불러와지지 않음
200
2018년 06월의 W6X001자료가 불러와지지 않음
200
2018년 07월의 W6X001자료가 불러와지지 않음
200
2018년 08월의 W6X001자료가 불러와지지 않음
200
2018년 09월의 W6X001자료가 불러와지지 않음
200
2018년 10월의 W6X001자료가 불러와지지 않음
200
2018년 11월의 W6X001자료가 불러와지지 않음
200
2018년 12월의 W6X001자료가 불러와지지 않음
200
2019년 01월의 W6X001자료가 불러와지지 않음
200
2019년 02월의 W6X001자료가 불러와지지 않음
200
2019년 03월의 W6X001자료가 불러와지지 않음
200
2019년 04월의 W6X001자료가 불러와지지 않음
200
2019년 05월의 W6X001자료가 불러와지지 않음
200
2019년 06월의 W6X001자료가 불러와지지 않음
200
2019년 07월의 W6X001자료가 불러와지지 않음
200
2019년 08월의 W6X001자료가 불러와지지 않음
200
2019년 09월의 W6X001자료가 불러와지지 않음
200
2019년 10월의 W6X001자료가 불러와지지 않음
200
2019년 11월의 W6X001자료가 불러와지지 않음
200
2019년 12월의 W6X001자료가 불러와지지 않음
200
2020년 01월의 W6X001자료가 불러와지지 않음
200
2020년 02월의 W6X001자료가 불러와지지 않음
200
2020년 03월의 W6X001자료가 불러와지지 않음
200
2020년 04월의 W6X001자료가 불러와지지 않음
200
2020년 05월의 W6X001자료가 불러와지지 않음
200
2020년 06월의

200
2020년 11월의 W6X006자료가 불러와지지 않음
200
2020년 12월의 W6X006자료가 불러와지지 않음
200
2021년 01월의 W6X006자료가 불러와지지 않음
200
2021년 02월의 W6X006자료가 불러와지지 않음
200
2021년 03월의 W6X006자료가 불러와지지 않음
200
2021년 04월의 W6X006자료가 불러와지지 않음
200
2021년 05월의 W6X006자료가 불러와지지 않음
200
2021년 06월의 W6X006자료가 불러와지지 않음
200
2018년 01월의 W6X007자료가 불러와지지 않음
200
2018년 02월의 W6X007자료가 불러와지지 않음
200
2018년 03월의 W6X007자료가 불러와지지 않음
200
2018년 04월의 W6X007자료가 불러와지지 않음
200
2018년 05월의 W6X007자료가 불러와지지 않음
200
2018년 06월의 W6X007자료가 불러와지지 않음
200
2018년 07월의 W6X007자료가 불러와지지 않음
200
2018년 08월의 W6X007자료가 불러와지지 않음
200
2018년 09월의 W6X007자료가 불러와지지 않음
200
2018년 10월의 W6X007자료가 불러와지지 않음
200
2018년 11월의 W6X007자료가 불러와지지 않음
200
2018년 12월의 W6X007자료가 불러와지지 않음
200
2019년 01월의 W6X007자료가 불러와지지 않음
200
2019년 02월의 W6X007자료가 불러와지지 않음
200
2019년 03월의 W6X007자료가 불러와지지 않음
200
2019년 04월의 W6X007자료가 불러와지지 않음
200
2019년 05월의 W6X007자료가 불러와지지 않음
200
2019년 06월의 W6X007자료가 불러와지지 않음
200
2019년 07월의 W6X007자료가 불러와지지 않음
200
2019년 08월의 W6X007자료가 불러와지지 않음
200
2019년 09월의 W6X007자료가 불러와지지 않음
200
2019년 10월의

200
2020년 03월의 W6X00D자료가 불러와지지 않음
200
2020년 04월의 W6X00D자료가 불러와지지 않음
200
2020년 05월의 W6X00D자료가 불러와지지 않음
200
2020년 06월의 W6X00D자료가 불러와지지 않음
200
2020년 07월의 W6X00D자료가 불러와지지 않음
200
2020년 08월의 W6X00D자료가 불러와지지 않음
200
2020년 09월의 W6X00D자료가 불러와지지 않음
200
2020년 10월의 W6X00D자료가 불러와지지 않음
200
2020년 11월의 W6X00D자료가 불러와지지 않음
200
2020년 12월의 W6X00D자료가 불러와지지 않음
200
2021년 01월의 W6X00D자료가 불러와지지 않음
200
2021년 02월의 W6X00D자료가 불러와지지 않음
200
2021년 03월의 W6X00D자료가 불러와지지 않음
200
2021년 04월의 W6X00D자료가 불러와지지 않음
200
2021년 05월의 W6X00D자료가 불러와지지 않음
200
2021년 06월의 W6X00D자료가 불러와지지 않음
200
2018년 01월의 W6X00E자료가 불러와지지 않음
200
2018년 02월의 W6X00E자료가 불러와지지 않음
200
2018년 03월의 W6X00E자료가 불러와지지 않음
200
2018년 04월의 W6X00E자료가 불러와지지 않음
200
2018년 05월의 W6X00E자료가 불러와지지 않음
200
2018년 06월의 W6X00E자료가 불러와지지 않음
200
2018년 07월의 W6X00E자료가 불러와지지 않음
200
2018년 08월의 W6X00E자료가 불러와지지 않음
200
2018년 09월의 W6X00E자료가 불러와지지 않음
200
2018년 10월의 W6X00E자료가 불러와지지 않음
200
2018년 11월의 W6X00E자료가 불러와지지 않음
200
2018년 12월의 W6X00E자료가 불러와지지 않음
200
2019년 01월의 W6X00E자료가 불러와지지 않음
200
2019년 02월의

200
2019년 05월의 W6X014자료가 불러와지지 않음
200
2019년 06월의 W6X014자료가 불러와지지 않음
200
2019년 07월의 W6X014자료가 불러와지지 않음
200
2019년 08월의 W6X014자료가 불러와지지 않음
200
2019년 09월의 W6X014자료가 불러와지지 않음
200
2019년 10월의 W6X014자료가 불러와지지 않음
200
2019년 11월의 W6X014자료가 불러와지지 않음
200
2019년 12월의 W6X014자료가 불러와지지 않음
200
2020년 01월의 W6X014자료가 불러와지지 않음
200
2020년 02월의 W6X014자료가 불러와지지 않음
200
2020년 03월의 W6X014자료가 불러와지지 않음
200
2020년 04월의 W6X014자료가 불러와지지 않음
200
2020년 05월의 W6X014자료가 불러와지지 않음
200
2020년 06월의 W6X014자료가 불러와지지 않음
200
2020년 07월의 W6X014자료가 불러와지지 않음
200
2020년 08월의 W6X014자료가 불러와지지 않음
200
2020년 09월의 W6X014자료가 불러와지지 않음
200
2020년 10월의 W6X014자료가 불러와지지 않음
200
2020년 11월의 W6X014자료가 불러와지지 않음
200
2020년 12월의 W6X014자료가 불러와지지 않음
200
2021년 01월의 W6X014자료가 불러와지지 않음
200
2021년 02월의 W6X014자료가 불러와지지 않음
200
2021년 03월의 W6X014자료가 불러와지지 않음
200
2021년 04월의 W6X014자료가 불러와지지 않음
200
2021년 05월의 W6X014자료가 불러와지지 않음
200
2021년 06월의 W6X014자료가 불러와지지 않음
200
2018년 01월의 W6X015자료가 불러와지지 않음
200
2018년 02월의 W6X015자료가 불러와지지 않음
200
2018년 03월의 W6X015자료가 불러와지지 않음
200
2018년 04월의

200
2018년 07월의 W6X01A자료가 불러와지지 않음
200
2018년 08월의 W6X01A자료가 불러와지지 않음
200
2018년 09월의 W6X01A자료가 불러와지지 않음
200
2018년 10월의 W6X01A자료가 불러와지지 않음
200
2018년 11월의 W6X01A자료가 불러와지지 않음
200
2018년 12월의 W6X01A자료가 불러와지지 않음
200
2019년 01월의 W6X01A자료가 불러와지지 않음
200
2019년 02월의 W6X01A자료가 불러와지지 않음
200
2019년 03월의 W6X01A자료가 불러와지지 않음
200
2019년 04월의 W6X01A자료가 불러와지지 않음
200
2019년 05월의 W6X01A자료가 불러와지지 않음
200
2019년 06월의 W6X01A자료가 불러와지지 않음
200
2019년 07월의 W6X01A자료가 불러와지지 않음
200
2019년 08월의 W6X01A자료가 불러와지지 않음
200
2019년 09월의 W6X01A자료가 불러와지지 않음
200
2019년 10월의 W6X01A자료가 불러와지지 않음
200
2019년 11월의 W6X01A자료가 불러와지지 않음
200
2019년 12월의 W6X01A자료가 불러와지지 않음
200
2020년 01월의 W6X01A자료가 불러와지지 않음
200
2020년 02월의 W6X01A자료가 불러와지지 않음
200
2020년 03월의 W6X01A자료가 불러와지지 않음
200
2020년 04월의 W6X01A자료가 불러와지지 않음
200
2020년 05월의 W6X01A자료가 불러와지지 않음
200
2020년 06월의 W6X01A자료가 불러와지지 않음
200
2020년 07월의 W6X01A자료가 불러와지지 않음
200
2020년 08월의 W6X01A자료가 불러와지지 않음
200
2020년 09월의 W6X01A자료가 불러와지지 않음
200
2020년 10월의 W6X01A자료가 불러와지지 않음
200
2020년 11월의 W6X01A자료가 불러와지지 않음
200
2020년 12월의

...

200
2018년 06월의 W6XFD3자료가 불러와지지 않음
200
2018년 07월의 W6XFD3자료가 불러와지지 않음
200
2018년 08월의 W6XFD3자료가 불러와지지 않음
200
2018년 09월의 W6XFD3자료가 불러와지지 않음
200
2018년 10월의 W6XFD3자료가 불러와지지 않음
200
2018년 11월의 W6XFD3자료가 불러와지지 않음
200
2018년 12월의 W6XFD3자료가 불러와지지 않음
200
2019년 01월의 W6XFD3자료가 불러와지지 않음
200
2019년 02월의 W6XFD3자료가 불러와지지 않음
200
2019년 03월의 W6XFD3자료가 불러와지지 않음
200
2019년 04월의 W6XFD3자료가 불러와지지 않음
200
2019년 05월의 W6XFD3자료가 불러와지지 않음
200
2019년 06월의 W6XFD3자료가 불러와지지 않음
200
2019년 07월의 W6XFD3자료가 불러와지지 않음
200
2019년 08월의 W6XFD3자료가 불러와지지 않음
200
2019년 09월의 W6XFD3자료가 불러와지지 않음
200
2019년 10월의 W6XFD3자료가 불러와지지 않음
200
2019년 11월의 W6XFD3자료가 불러와지지 않음
200
2019년 12월의 W6XFD3자료
200
2020년 01월의 W6XFD3자료
200
2020년 02월의 W6XFD3자료
200
2020년 03월의 W6XFD3자료
200
2020년 04월의 W6XFD3자료
200
2020년 05월의 W6XFD3자료
200
2020년 06월의 W6XFD3자료
200
2020년 07월의 W6XFD3자료
200
2020년 08월의 W6XFD3자료
200
2020년 09월의 W6XFD3자료
200
2020년 10월의 W6XFD3자료
200
2020년 11월의 W6XFD3자료
200
2020년 12월의 W6XFD3자료
200
2021년 01월의 W6XFD3자료
200
2021년 02월의 W6XFD3자료
200
2021년 03월의 W6XFD3자료
200


200
2019년 11월의 W6XFD9자료가 불러와지지 않음
200
2019년 12월의 W6XFD9자료가 불러와지지 않음
200
2020년 01월의 W6XFD9자료
200
2020년 02월의 W6XFD9자료
200
2020년 03월의 W6XFD9자료
200
2020년 04월의 W6XFD9자료
200
2020년 05월의 W6XFD9자료
200
2020년 06월의 W6XFD9자료
200
2020년 07월의 W6XFD9자료
200
2020년 08월의 W6XFD9자료
200
2020년 09월의 W6XFD9자료
200
2020년 10월의 W6XFD9자료
200
2020년 11월의 W6XFD9자료
200
2020년 12월의 W6XFD9자료
200
2021년 01월의 W6XFD9자료
200
2021년 02월의 W6XFD9자료
200
2021년 03월의 W6XFD9자료
200
2021년 04월의 W6XFD9자료가 불러와지지 않음
200
2021년 05월의 W6XFD9자료
200
2021년 06월의 W6XFD9자료
200
2018년 01월의 W6XFE1자료가 불러와지지 않음
200
2018년 02월의 W6XFE1자료가 불러와지지 않음
200
2018년 03월의 W6XFE1자료가 불러와지지 않음
200
2018년 04월의 W6XFE1자료가 불러와지지 않음
200
2018년 05월의 W6XFE1자료가 불러와지지 않음
200
2018년 06월의 W6XFE1자료가 불러와지지 않음
200
2018년 07월의 W6XFE1자료가 불러와지지 않음
200
2018년 08월의 W6XFE1자료가 불러와지지 않음
200
2018년 09월의 W6XFE1자료가 불러와지지 않음
200
2018년 10월의 W6XFE1자료가 불러와지지 않음
200
2018년 11월의 W6XFE1자료가 불러와지지 않음
200
2018년 12월의 W6XFE1자료가 불러와지지 않음
200
2019년 01월의 W6XFE1자료가 불러와지지 않음
200
2019년 02월의 W6XFE1자료가 불러와지지 않음
200
2019년 03월의

200
2018년 08월의 W6XFE7자료가 불러와지지 않음
200
2018년 09월의 W6XFE7자료가 불러와지지 않음
200
2018년 10월의 W6XFE7자료가 불러와지지 않음
200
2018년 11월의 W6XFE7자료가 불러와지지 않음
200
2018년 12월의 W6XFE7자료가 불러와지지 않음
200
2019년 01월의 W6XFE7자료가 불러와지지 않음
200
2019년 02월의 W6XFE7자료가 불러와지지 않음
200
2019년 03월의 W6XFE7자료가 불러와지지 않음
200
2019년 04월의 W6XFE7자료가 불러와지지 않음
200
2019년 05월의 W6XFE7자료가 불러와지지 않음
200
2019년 06월의 W6XFE7자료가 불러와지지 않음
200
2019년 07월의 W6XFE7자료가 불러와지지 않음
200
2019년 08월의 W6XFE7자료가 불러와지지 않음
200
2019년 09월의 W6XFE7자료가 불러와지지 않음
200
2019년 10월의 W6XFE7자료가 불러와지지 않음
200
2019년 11월의 W6XFE7자료가 불러와지지 않음
200
2019년 12월의 W6XFE7자료
200
2020년 01월의 W6XFE7자료
200
2020년 02월의 W6XFE7자료
200
2020년 03월의 W6XFE7자료
200
2020년 04월의 W6XFE7자료
200
2020년 05월의 W6XFE7자료
200
2020년 06월의 W6XFE7자료
200
2020년 07월의 W6XFE7자료
200
2020년 08월의 W6XFE7자료
200
2020년 09월의 W6XFE7자료
200
2020년 10월의 W6XFE7자료
200
2020년 11월의 W6XFE7자료
200
2020년 12월의 W6XFE7자료
200
2021년 01월의 W6XFE7자료
200
2021년 02월의 W6XFE7자료
200
2021년 03월의 W6XFE7자료
200
2021년 04월의 W6XFE7자료가 불러와지지 않음
200
2021년 05월의 W6XFE7자료
200
2021년 06월의

200
2019년 11월의 W6XFF4자료가 불러와지지 않음
200
2019년 12월의 W6XFF4자료가 불러와지지 않음
200
2020년 01월의 W6XFF4자료
200
2020년 02월의 W6XFF4자료
200
2020년 03월의 W6XFF4자료
200
2020년 04월의 W6XFF4자료
200
2020년 05월의 W6XFF4자료
200
2020년 06월의 W6XFF4자료
200
2020년 07월의 W6XFF4자료
200
2020년 08월의 W6XFF4자료
200
2020년 09월의 W6XFF4자료
200
2020년 10월의 W6XFF4자료
200
2020년 11월의 W6XFF4자료
200
2020년 12월의 W6XFF4자료
200
2021년 01월의 W6XFF4자료
200
2021년 02월의 W6XFF4자료
200
2021년 03월의 W6XFF4자료
200
2021년 04월의 W6XFF4자료가 불러와지지 않음
200
2021년 05월의 W6XFF4자료
200
2021년 06월의 W6XFF4자료
200
2018년 01월의 W6XFF5자료가 불러와지지 않음
200
2018년 02월의 W6XFF5자료가 불러와지지 않음
200
2018년 03월의 W6XFF5자료가 불러와지지 않음
200
2018년 04월의 W6XFF5자료가 불러와지지 않음
200
2018년 05월의 W6XFF5자료가 불러와지지 않음
200
2018년 06월의 W6XFF5자료가 불러와지지 않음
200
2018년 07월의 W6XFF5자료가 불러와지지 않음
200
2018년 08월의 W6XFF5자료가 불러와지지 않음
200
2018년 09월의 W6XFF5자료가 불러와지지 않음
200
2018년 10월의 W6XFF5자료가 불러와지지 않음
200
2018년 11월의 W6XFF5자료가 불러와지지 않음
200
2018년 12월의 W6XFF5자료가 불러와지지 않음
200
2019년 01월의 W6XFF5자료가 불러와지지 않음
200
2019년 02월의 W6XFF5자료가 불러와지지 않음
200
2019년 03월의

200
2018년 08월의 W6XFFB자료가 불러와지지 않음
200
2018년 09월의 W6XFFB자료가 불러와지지 않음
200
2018년 10월의 W6XFFB자료가 불러와지지 않음
200
2018년 11월의 W6XFFB자료가 불러와지지 않음
200
2018년 12월의 W6XFFB자료가 불러와지지 않음
200
2019년 01월의 W6XFFB자료가 불러와지지 않음
200
2019년 02월의 W6XFFB자료가 불러와지지 않음
200
2019년 03월의 W6XFFB자료가 불러와지지 않음
200
2019년 04월의 W6XFFB자료가 불러와지지 않음
200
2019년 05월의 W6XFFB자료가 불러와지지 않음
200
2019년 06월의 W6XFFB자료가 불러와지지 않음
200
2019년 07월의 W6XFFB자료가 불러와지지 않음
200
2019년 08월의 W6XFFB자료가 불러와지지 않음
200
2019년 09월의 W6XFFB자료가 불러와지지 않음
200
2019년 10월의 W6XFFB자료가 불러와지지 않음
200
2019년 11월의 W6XFFB자료가 불러와지지 않음
200
2019년 12월의 W6XFFB자료가 불러와지지 않음
200
2020년 01월의 W6XFFB자료
200
2020년 02월의 W6XFFB자료
200
2020년 03월의 W6XFFB자료
200
2020년 04월의 W6XFFB자료
200
2020년 05월의 W6XFFB자료
200
2020년 06월의 W6XFFB자료
200
2020년 07월의 W6XFFB자료
200
2020년 08월의 W6XFFB자료
200
2020년 09월의 W6XFFB자료
200
2020년 10월의 W6XFFB자료
200
2020년 11월의 W6XFFB자료
200
2020년 12월의 W6XFFB자료
200
2021년 01월의 W6XFFB자료
200
2021년 02월의 W6XFFB자료
200
2021년 03월의 W6XFFB자료
200
2021년 04월의 W6XFFB자료가 불러와지지 않음
200
2021년 05월의 W6XFFB자료
200


- 저장된 자료를 바탕으로 병합+월별 읍면동 파일로 만드는 작업을 해봄

In [41]:
rfid=pd.concat([df_new_je,df_new_su],axis=0)
rfid

base_date aptCode emd_nm  disQuantity  disCount
0       2018-01  W6X001    건입동          NaN       NaN
1       2018-02  W6X001    건입동          NaN       NaN
2       2018-03  W6X001    건입동          NaN       NaN
3       2018-04  W6X001    건입동          NaN       NaN
4       2018-05  W6X001    건입동          NaN       NaN
...         ...     ...    ...          ...       ...
28639   2021-02  W6Y74B    동홍동          NaN       NaN
28640   2021-03  W6Y74B    동홍동          NaN       NaN
28641   2021-04  W6Y74B    동홍동          NaN       NaN
28642   2021-05  W6Y74B    동홍동          NaN       NaN
28643   2021-06  W6Y74B    동홍동          NaN       NaN

[108990 rows x 5 columns]

In [48]:
rfid_group=rfid.groupby(['base_date','emd_nm']).sum()
rfid_group

base_date emd_nm  disQuantity  disCount
0      2018-01    건입동   37487850.0   14736.0
1      2018-01    구좌읍          0.0       0.0
2      2018-01    남원읍   42989050.0    9946.0
3      2018-01    노형동  285167500.0  121261.0
4      2018-01    대륜동   51137250.0   18624.0
...        ...    ...          ...       ...
1759   2021-06    표선면   41201100.0   10305.0
1760   2021-06    한경면   25355150.0    7557.0
1761   2021-06    한림읍   83268690.0   24862.0
1762   2021-06    화북동  112522450.0   67508.0
1763   2021-06    효돈동   28042550.0    8883.0

[1764 rows x 4 columns]

### 3. 결측치 채우기

- 결측치를 각 읍면동의 평균값으로 대체하는 작업이 필요할 것
  - 몇몇 데이터에 한하여 결측치가 존재하는 것을 알게 됨

In [69]:
rfid_group.replace(0,np.nan)#0값을 결측치로 

base_date emd_nm  disQuantity  disCount
0      2018-01    건입동   37487850.0   14736.0
1      2018-01    구좌읍          NaN       NaN
2      2018-01    남원읍   42989050.0    9946.0
3      2018-01    노형동  285167500.0  121261.0
4      2018-01    대륜동   51137250.0   18624.0
...        ...    ...          ...       ...
1759   2021-06    표선면   41201100.0   10305.0
1760   2021-06    한경면   25355150.0    7557.0
1761   2021-06    한림읍   83268690.0   24862.0
1762   2021-06    화북동  112522450.0   67508.0
1763   2021-06    효돈동   28042550.0    8883.0

[1764 rows x 4 columns]

In [71]:
list_=[]
for value in dong:
    gu=rfid_group[rfid_group['emd_nm']==value].copy()
    gu.fillna(gu.mean(),inplace=True)#읍면동 평균
    list_.append(gu)
new_rfid=pd.concat(list_[:41])
new_rfid

base_date emd_nm  disQuantity  disCount
39     2018-01    한림읍          0.0       0.0
81     2018-02    한림읍          0.0       0.0
123    2018-03    한림읍          0.0       0.0
165    2018-04    한림읍          0.0       0.0
207    2018-05    한림읍          0.0       0.0
...        ...    ...          ...       ...
1576   2021-02    예래동   11363850.0    3233.0
1618   2021-03    예래동   12785800.0    3545.0
1660   2021-04    예래동          0.0       0.0
1702   2021-05    예래동   13604500.0    4393.0
1744   2021-06    예래동   12490100.0    4263.0

[1722 rows x 4 columns]

In [77]:
rfid_group=new_rfid.groupby(['base_date','emd_nm']).sum()
rfid_group.replace(0,np.nan,inplace=True)
rfid_group.fillna(rfid_group.mean(),inplace=True)
rfid_group.to_csv("./datas/rfid_group.csv")

- 관련 RFID 값까지 저장하게 되면 모든 전처리 과정 종료